In [1]:
import json

path = "/mnt/hdd1/ljiahao/xianglin/llm-as-a-judge-attack/trajectories/ucb_2025-07-30_23:25:40.json"
with open(path, "r") as f:
    metadata = json.load(f)

metadata

{'strategy': 'UCB',
 'judge_type': 'pointwise',
 'answer_position': None,
 'dataset_name': 'AlpacaEval',
 'judge_backbone': 'gemini-2.0-flash',
 'baseline_response_model_name': None,
 'llm_agent_name': 'gpt-4.1-nano',
 'response_model_name': 'gpt-4o-mini',
 'test_mode': 'single',
 'lambda_reg': 1.0,
 'n_features': 384,
 'budget': 20,
 'pool_size': 3,
 'eval_num': 248,
 'reward_type': 'absolute',
 'alpha': 1.0,
 'timestamp': '2025-07-30 23:25:40',
 'time_taken': 1674.5186893939972,
 'trajectories': [{'question': 'What are the names of some famous actors that started their careers on Broadway?',
   'best_path': [9,
    [9,
     'The response is relevant and accurate, providing a list of actors who started on Broadway and transitioned to film/TV. The descriptions for each actor are accurate and include specific Broadway productions. The response is well-organized and easy to read. The response is comprehensive and includes a good variety of actors.',
     'Many famous actors began their c

In [2]:
old_judge = metadata["judge_backbone"]
trajectories = metadata["trajectories"]

question_list = [trajectory["question"] for trajectory in trajectories]
init_response_list = [trajectory["best_path"][1][2] for trajectory in trajectories]
final_response_list = [trajectory["best_path"][-1][2] for trajectory in trajectories]
init_score_list = [trajectory["best_path"][1][0] for trajectory in trajectories]
final_score_list = [trajectory["best_path"][-1][0] for trajectory in trajectories]

In [3]:
from src.llm_evaluator import JudgeType, load_judge_model

new_judge_type = JudgeType.POINTWISE

new_judge_backbone = "gpt-4.1"
new_judge = load_judge_model(new_judge_type, new_judge_backbone)

2025-07-31 10:31:08.737479: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:467] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1753929068.750326 3023105 cuda_dnn.cc:8579] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1753929068.754092 3023105 cuda_blas.cc:1407] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
W0000 00:00:1753929068.765403 3023105 computation_placer.cc:177] computation placer already registered. Please check linkage and avoid linking the same target more than once.
W0000 00:00:1753929068.765414 3023105 computation_placer.cc:177] computation placer already registered. Please check linkage and avoid linking the same target more than once.
W0000 00:00:1753929068.765416 3023105 computation_placer.cc:177] computation placer alr

INFO 07-31 10:31:10 [__init__.py:235] Automatically detected platform cuda.


In [4]:
old_scores, old_explanations = await new_judge.batch_get_score(question_list, init_response_list)
new_scores, new_explanations = await new_judge.batch_get_score(question_list, final_response_list)

Could not find/parse any valid JSON in the provided text.
Could not find/parse any valid JSON in the provided text.
Could not find/parse any valid JSON in the provided text.
Could not find/parse any valid JSON in the provided text.
Could not find/parse any valid JSON in the provided text.
Could not find/parse any valid JSON in the provided text.


In [11]:
import numpy as np

higher_idxs = np.array([i for i in range(len(final_score_list)) if final_score_list[i] > init_score_list[i]])

lower_idxs = np.array([i for i in range(len(final_score_list)) if final_score_list[i] < init_score_list[i]])

tie_idxs = np.array([i for i in range(len(final_score_list)) if final_score_list[i] == init_score_list[i]])


In [12]:
higher_diff = np.array([new_scores[i] - old_scores[i] for i in higher_idxs])
lower_diff = np.array([new_scores[i] - old_scores[i] for i in lower_idxs])
tie_diff = np.array([new_scores[i] - old_scores[i] for i in tie_idxs])

np.mean(higher_diff), np.mean(lower_diff), np.mean(tie_diff), len(higher_diff), len(lower_diff), len(tie_diff)

(np.float64(-0.23220973782771537),
 np.float64(0.0),
 np.float64(-0.2126865671641791),
 267,
 2,
 536)

In [15]:
np.sum(higher_diff>0),np.sum(higher_diff==0), np.sum(higher_diff<0), np.sum(lower_diff>0), np.sum(lower_diff==0), np.sum(lower_diff<0), np.sum(tie_diff>0), np.sum(tie_diff==0), np.sum(tie_diff<0)

(np.int64(31),
 np.int64(168),
 np.int64(68),
 np.int64(0),
 np.int64(2),
 np.int64(0),
 np.int64(35),
 np.int64(354),
 np.int64(147))

In [7]:
diff = [new_score - old_score for new_score, old_score in zip(new_scores, old_scores)]

sum(d>0 for d in diff)/len(diff)

0.08198757763975155